In [6]:
import vectorbtpro as vbt
#from vectorbtpro import *
import os
import numpy as np
import talib
from numba import njit


In [5]:
pip list

Package                                  Version              Editable project location
---------------------------------------- -------------------- -----------------------------------------------------------------------
agentops                                 0.3.17
aiohappyeyeballs                         2.4.3
aiohttp                                  3.10.10
aiosignal                                1.3.1
alembic                                  1.14.0
annotated-types                          0.7.0
anyio                                    4.6.2.post1
appdirs                                  1.4.4
arch                                     7.1.0
argon2-cffi                              23.1.0
argon2-cffi-bindings                     21.2.0
arrow                                    1.3.0
asgiref                                  3.8.1
astropy                                  6.1.4
astropy-iers-data                        0.2024.10.21.0.33.21
asttokens                                2.4.1

# CONFIGURAÇÃO


In [7]:
'''vbt.settings.execution.engine = 'serial'


# Configurações válidas de caching e chunking
vbt.settings.caching.update({
    'disable': False,
    'use_cached_accessors': True
})

vbt.settings.execution.update({
    'cache_chunks': True,
    'chunk_cache_dir': "cache_chunks",
    'release_chunk_cache': True
})
'''
vbt.settings.set_theme("dark")

# CARREGAR DADOS


In [12]:
# Carregando os dados de preços usando SerialEngine
DB_PATH = "odysseus/forex_market.duckdb"
symbol = "EURUSD"
data = vbt.DuckDBData.from_duckdb(symbol, start="2013-01-01", connection=DB_PATH)
print(data.close)
print(data.stats())

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

datetime
2013-01-01 17:00:00+00:00    1.32034
2013-01-01 17:01:00+00:00    1.32046
2013-01-01 17:02:00+00:00    1.32050
2013-01-01 17:03:00+00:00    1.32025
2013-01-01 17:04:00+00:00    1.32025
                              ...   
2023-12-29 16:54:00+00:00    1.10388
2023-12-29 16:55:00+00:00    1.10395
2023-12-29 16:56:00+00:00    1.10370
2023-12-29 16:57:00+00:00    1.10366
2023-12-29 16:58:00+00:00    1.10361
Name: close, Length: 4035789, dtype: float64
Start Index            2013-01-01 17:00:00+00:00
End Index              2023-12-29 16:58:00+00:00
Total Duration                2802 days 15:09:00
Total Symbols                                  1
Null Counts: EURUSD                            0
Name: agg_stats, dtype: object


In [11]:
%pwd

'D:\\Caleb\\caleb\\Python\\mercado\\mercado\\ulysses\\vectorbt_pro\\vectorbt.pro'

# RESAMPLE


In [51]:
time_frames = [1, 4, 24]
freqs = [f'{tf}h' for tf in time_frames]
h1_data = data.resample("1h")
h1_close = h1_data.close
h4_data = data.resample("4h")
h4_close = h4_data.close
h24_data = data.resample("24h")
h24_close = h24_data.close

print(h1_data.stats())
h24_data.plot().show()

Start Index            2013-01-01 17:00:00+00:00
End Index              2023-12-29 16:00:00+00:00
Total Duration                4014 days 00:00:00
Total Symbols                                  1
Null Counts: EURUSD                       143815
Name: agg_stats, dtype: object


# Indicador de tendência

In [52]:
high = h24_data.high.ffill().bfill()
low = h24_data.low.ffill().bfill()
close = h24_close.ffill().bfill()

In [53]:
def get_basic_bands(med_price, atr, multiplier):
    matr = multiplier * atr
    upper = med_price + matr
    lower = med_price - matr
    return upper, lower

In [54]:
@njit
def get_final_bands_nb(close, upper, lower):
    trend = np.full(close.shape, np.nan)
    dir_ = np.full(close.shape, 1)
    long = np.full(close.shape, np.nan)
    short = np.full(close.shape, np.nan)

    for i in range(1, close.shape[0]):
        if close[i] > upper[i - 1]:
            dir_[i] = 1
        elif close[i] < lower[i - 1]:
            dir_[i] = -1
        else:
            dir_[i] = dir_[i - 1]
            if dir_[i] > 0 and lower[i] < lower[i - 1]:
                lower[i] = lower[i - 1]
            if dir_[i] < 0 and upper[i] > upper[i - 1]:
                upper[i] = upper[i - 1]

        if dir_[i] > 0:
            trend[i] = long[i] = lower[i]
        else:
            trend[i] = short[i] = upper[i]
            
    return trend, dir_, long, short

In [56]:
def faster_supertrend_talib(high, low, close, period=7, multiplier=3):
    avg_price = talib.MEDPRICE(high, low)
    atr = talib.ATR(high, low, close, period)
    upper, lower = get_basic_bands(avg_price, atr, multiplier)
    return get_final_bands_nb(close, upper, lower)

In [57]:
# Executando o faster_supertrend_talib
trend, dir_, long, short = faster_supertrend_talib(
    high.values, 
    low.values, 
    close.values
)


valid_mask = np.isfinite(trend)
print("Valores válidos do trend:")
print(trend[valid_mask])
print(len(trend[valid_mask]))
print("\nDireção correspondente:")
print(dir_[valid_mask])
print(len(dir_[valid_mask]))
print("\nValores long válidos:")
print(long[np.isfinite(long)])
print(len(long[valid_mask]))
print("\nValores short válidos:")
print(short[np.isfinite(short)])
print(len(short[valid_mask]))

Valores válidos do trend:
[1.27730714 1.27730714 1.28012688 ... 1.09135173 1.09189434 1.09189434]
4008

Direção correspondente:
[1 1 1 ... 1 1 1]
4008

Valores long válidos:
[1.27730714 1.27730714 1.28012688 ... 1.09135173 1.09189434 1.09189434]
4008

Valores short válidos:
[1.37236903 1.37085774 1.36493877 ... 1.0922808  1.0922808  1.0922808 ]
4008


In [58]:
SuperTrend = vbt.IF(
    class_name='SuperTrend',
    short_name='st',
    input_names=['high', 'low', 'close'],
    param_names=['period', 'multiplier'],
    output_names=['supert', 'superd', 'superl', 'supers']
).with_apply_func(
    faster_supertrend_talib, 
    takes_1d=True,
    period=7, 
    multiplier=3
)

In [61]:
class SuperTrend(SuperTrend):
    def plot(self, 
             column=None, 
             close_kwargs=None,
             superl_kwargs=None,
             supers_kwargs=None,
             fig=None, 
             **layout_kwargs):
        close_kwargs = close_kwargs if close_kwargs else {}
        superl_kwargs = superl_kwargs if superl_kwargs else {}
        supers_kwargs = supers_kwargs if supers_kwargs else {}
        
        close = self.select_col_from_obj(self.close, column).rename('Close')
        supers = self.select_col_from_obj(self.supers, column).rename('Short')
        superl = self.select_col_from_obj(self.superl, column).rename('Long')
        
        fig = close.vbt.plot(fig=fig, **close_kwargs, **layout_kwargs)
        supers.vbt.plot(fig=fig, **supers_kwargs)
        superl.vbt.plot(fig=fig, **superl_kwargs)
        
        return fig

## Otimização

In [78]:
periods = np.arange(80, 100)
multipliers = np.arange(50, 80) / 10

In [79]:
st = SuperTrend.run(
    high, low, close, 
    period=periods, 
    multiplier=multipliers,
    param_product=True,
)
print(st.supert.dropna())

st_period                        80                                          \
st_multiplier                   5.0       5.1       5.2       5.3       5.4   
datetime                                                                      
2013-04-10 00:00:00+00:00  1.257171  1.256150  1.255129  1.254108  1.253088   
2013-04-11 00:00:00+00:00  1.258798  1.257780  1.256762  1.255744  1.254725   
2013-04-12 00:00:00+00:00  1.258798  1.257780  1.256762  1.255744  1.254725   
2013-04-13 00:00:00+00:00  1.258798  1.257780  1.256762  1.255744  1.254725   
2013-04-14 00:00:00+00:00  1.258798  1.257780  1.256762  1.255744  1.254725   
...                             ...       ...       ...       ...       ...   
2023-12-25 00:00:00+00:00  1.069162  1.068519  1.067876  1.067234  1.066591   
2023-12-26 00:00:00+00:00  1.070710  1.070071  1.069432  1.068793  1.068153   
2023-12-27 00:00:00+00:00  1.075846  1.075204  1.074562  1.073920  1.073278   
2023-12-28 00:00:00+00:00  1.077501  1.076857  1.076

In [80]:
# Escolha um período e multiplicador específico
periodos = [periods[0], periods[-1]]
multiplicadores = [multipliers[0], multipliers[-1]]

# Criando todas as combinações possíveis
combinacoes = [
    (periodos[0], multiplicadores[0]),  # (4, 2.0)
    (periodos[0], multiplicadores[-1]), # (4, 4.0)
    (periodos[-1], multiplicadores[0]), # (19, 2.0)
    (periodos[-1], multiplicadores[-1]) # (19, 4.0)
]

# Plotando cada combinação separadamente
for periodo, multiplicador in combinacoes:
    st.plot(
        column=(periodo, multiplicador),
        superl_kwargs=dict(trace_kwargs=dict(line_color='limegreen')),
        supers_kwargs=dict(trace_kwargs=dict(line_color='red')),
        title=f'SuperTrend - Período: {periodo}, Multiplicador: {multiplicador}'
    ).show()

# Backtesting

In [82]:
entries = (~st.superl.isnull()).vbt.signals.fshift()
exits = (~st.supers.isnull()).vbt.signals.fshift()

In [83]:
pf = vbt.Portfolio.from_signals(close, entries, exits, init_cash=100, fees=0.001, freq='1D')

In [84]:
print(symbol)
pf.final_value.vbt.heatmap(
    x_level='st_period', 
    y_level='st_multiplier'
).show()

EURUSD


In [85]:
vbt.Portfolio.from_holding(close, freq='1D').final_value

83.2278791261001